In [1]:
import pandas as pd 
from datetime import datetime
from dateutil.relativedelta import relativedelta

from utils.fetch_data import DataExtractor
from utils.eol_process import EOLHandler
from input_preprocess.iiot_preprocess import DataPreprocessor
from benchmark_data.benchmark_process import BenchmarkProcessor
from main.main_pipe import ForecastPIPE

### Ｄata Extractor 

In [2]:
data_extractor = DataExtractor()
product_info = data_extractor.get_product_info()
previous_year = (data_extractor.today_date + relativedelta(years=-3)).strftime('%Y/%m/01')
so_data = data_extractor.get_so_data(previous_year)
wo_data = data_extractor.get_wo_data(previous_year)
open_so_histo = data_extractor.get_openso(previous_year)
open_wo_histo = data_extractor.get_openwo(previous_year)
open_so_curr = data_extractor.get_openso_current()
open_wo_curr = data_extractor.get_openwo_current()

ZSTRATEGY_data = data_extractor.get_gai_data()
print(previous_year)

d:\SCM_indicator\utils\fetch_data.py:36: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  product_ori = pd.read_sql(sql_schema_product, self.extract_connection)
d:\SCM_indicator\utils\fetch_data.py:158: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  so_ori = pd.read_sql(sql_schema_so, self.extract_connection)
d:\SCM_indicator\utils\fetch_data.py:186: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  wo_ori = pd.read_sql(sql_schema_wo, self.extract_connection)
d:\SCM_indicator\utils\fetch_data.py:56: UserWarning: pandas only support

2022/03/01


In [3]:
data_extractor.save_to_csv(product_info, 'product_info')
data_extractor.save_to_csv(so_data, 'so_data')
data_extractor.save_to_csv(wo_data, 'wo_data')
data_extractor.save_to_csv(open_so_histo, 'open_so_histo')
data_extractor.save_to_csv(open_wo_histo, 'open_wo_histo')
data_extractor.save_to_csv(open_so_curr, 'open_so_curr')
data_extractor.save_to_csv(open_wo_curr, 'open_wo_curr')
data_extractor.save_to_csv(ZSTRATEGY_data, 'ZSTRATEGY_data')

NameError: name 'data_extractor' is not defined

In [2]:
so_data=pd.read_csv('Dataset\Fcst(proposed)\so_data_2025-03-01.csv')
wo_data=pd.read_csv('Dataset\Fcst(proposed)\wo_data_2025-03-01.csv')
product_info=pd.read_csv('Dataset\Fcst(proposed)\product_info_2025-03-01.csv')#
open_so_histo=pd.read_csv('Dataset\Fcst(proposed)\open_so_histo_2025-03-01.csv')
open_wo_histo=pd.read_csv('Dataset\Fcst(proposed)\open_wo_histo_2025-03-01.csv')
open_so_curr=pd.read_csv('Dataset\Fcst(proposed)\open_so_curr_2025-03-01.csv')
open_wo_curr=pd.read_csv('Dataset\Fcst(proposed)\open_wo_curr_2025-03-01.csv')
ZSTRATEGY_data=pd.read_csv('Dataset\Fcst(proposed)\ZSTRATEGY_data_2025-03-01.csv')

In [3]:
def select_aiflag(group):
    if 'Y' in group['AIFLAG'].values:
        return group[group['AIFLAG'] == 'Y'].iloc[0]
    else:
        selected_row = group.iloc[0]
        if pd.isna(selected_row['AIFLAG']):
            selected_row['AIFLAG'] = 'N'
        return selected_row
    
product_info = product_info.groupby('PART_NO').apply(select_aiflag).reset_index(drop=True)

In [ ]:
def create_full_data(data, full_date_range, qty_col):

    # 計算每個 PART_NO 和 year_month 的 ORDER_QTY 總和
    grouped_data = data.groupby(['PART_NO', 'year_month'])[qty_col].sum().reset_index()

    # 獲取所有的 PART_NO
    all_part_no = grouped_data['PART_NO'].unique()

    # 創建包含所有 PART_NO 和所有月份的完整日期範圍
    full_index = pd.MultiIndex.from_product([all_part_no, full_date_range], names=['PART_NO', 'year_month'])

    # 將總和結果與完整日期範圍合併
    full_data = grouped_data.set_index(['PART_NO', 'year_month']).reindex(full_index).fillna(0).reset_index()

    return full_data

def process_data(df, qty_col):
    # 重命名 PART_NO 為 MATNR
    p_df = df.pivot(index='PART_NO', columns='year_month', values=qty_col)
    p_df.columns.name = None
    p_df = p_df.reset_index()
    return p_df

### EOL

In [5]:
eol_handler =EOLHandler()
eol_handler.get_eol_data()
previous_year = (eol_handler.today_date + relativedelta(years=-3)).strftime('%Y/%m/01')

excluded_parts = ['EKI-2728-D']
filtered_part_numbers = eol_handler.eol_map_data.loc[
    ~eol_handler.eol_map_data.PART_NO_NEW.isin(excluded_parts), "PART_NO_OLD"
].tolist()

eol_so_data=eol_handler.get_target_so( previous_year, filtered_part_numbers) 
eol_wo_data=eol_handler.get_target_wo( previous_year, filtered_part_numbers)
eol_open_so_histo=eol_handler.get_target_open_so( previous_year, filtered_part_numbers)
eol_open_wo_histo=eol_handler.get_target_open_wo( previous_year, filtered_part_numbers)

combined_so_data = pd.concat([so_data, eol_so_data], ignore_index=True)
combined_wo_data = pd.concat([wo_data, eol_wo_data], ignore_index=True)
combined_open_so_histo = pd.concat([open_so_histo, eol_open_so_histo], ignore_index=True)
combined_open_wo_histo = pd.concat([open_wo_histo, eol_open_wo_histo], ignore_index=True)

d:\SCM_indicator\utils\eol_process.py:45: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  eol_ori = pd.read_sql(sql_schema_eol, self.extract_connection)
d:\SCM_indicator\utils\eol_process.py:48: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  eol['MATNR'] = eol['MATNR'].str.replace('\xa0', '', regex=False)
d:\SCM_indicator\utils\eol_process.py:49: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.h

          PART_NO_OLD      PART_NO_NEW LASTBUY_DATE
0     949NSSASM009091      EKI-2725-CE     20161230
1     949NSSASM007710    EKI-2741FI-BE     20170715
2     949NSSASM007310     EKI-2741F-BE     20170715
3     969NSEASM007710    EKI-2741FI-BE     20170715
4     969NSEASM007310     EKI-2741F-BE     20170715
...               ...              ...          ...
3320  PCIE-1203L-32AE   PCIE-1203L-32A     20240813
3321  PCIE-1203L-16AE   PCIE-1203L-16A     20240813
3322  PCIE-1203L-10AE   PCIE-1203L-10A     20240813
3323   AIMB-588Q-00A1  AIMB-588QM-0AB1     20241122
3324    PCIE-1672E-AE    PCIE-1672E-BE     20241231

[2509 rows x 3 columns]
                 PART_NO    PG                        PD PLM_STATUS  \
0         HPC-7120S-35ZB   ESG               Edge Server          A   
1        ASMB-786G2-00A1   ESG               Edge Server          A   
2      BB-SR30500120-SWH  ICWG           Cellular Router          N   
3     SQR-SD4M32G3K2SNCB  IPSG        Industrial Storage          A

d:\SCM_indicator\utils\eol_process.py:113: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  so_ori = pd.read_sql(sql_schema_so, self.extract_connection)
d:\SCM_indicator\utils\eol_process.py:124: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  wo_ori = pd.read_sql(sql_schema_wo, self.extract_connection)
d:\SCM_indicator\utils\eol_process.py:146: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  open_so_ori = pd.read_sql(sql_schema_open_so, self.extract_connection)
d:\SCM_indicator\utils\eol_process.py:157: UserWarning: pandas only s

In [ ]:
# list_part_no= eol_handler.eol_map_data.merge(
#     product_info[['PART_NO', 'AIFLAG']], 
#     left_on='PART_NO_NEW', 
#     right_on='PART_NO', 
#     how='left'  # 選擇合併方式，可改為 'inner', 'right', 'outer'
# ).query('AIFLAG=="Y"').PART_NO_NEW.unique()

In [6]:
from input_preprocess.opendata_process import OpenDataProcessor
exclude_month=(datetime.today()-relativedelta(months=1)).strftime('%Y/%m/01')
#open_so_histo
open_data_processor = OpenDataProcessor(combined_open_so_histo, combined_open_wo_histo)
combined_open_so_final, combined_open_wo_final= open_data_processor.get_realtime_data(open_so_curr,open_wo_curr, exclude_month)

exclude_version: 2025/02/01
exclude_version: 2025/02/01


### USAGE

##### get historical and backlog data 

In [9]:

# Create an instance of DataPreprocessor
preprocessor = DataPreprocessor(
    product_data=product_info,
    so_data=combined_so_data, 
    wo_data=combined_wo_data, 
    open_wo_data=combined_open_wo_final,
    open_so_data=combined_open_so_final
)

# Preprocess SO data
so_data_processed = preprocessor.so_data_preprocess()

# Preprocess WO data
wo_data_processed = preprocessor.wo_data_preprocess()

# Combine SO and WO data
used_data = preprocessor.merge_so_wo(so_data_processed, wo_data_processed)

# Merge open SO and WO data
open_data_list = [preprocessor.merge_open_so_wo(gap_year=i) for i in range(1, 7)]

##### actual demand

In [10]:
preprocessor_actual = DataPreprocessor(
    product_data=product_info,
    so_data=so_data,
    wo_data=wo_data,
    open_wo_data=open_wo_histo ,
    open_so_data=open_so_histo
)

# Combine SO and WO data
actual_data = preprocessor_actual.merge_so_wo(preprocessor_actual.so_data_preprocess(),preprocessor_actual.wo_data_preprocess())


##### parameter

In [11]:
# required_date started from 2024-07-01
# specified_month = '2024-11-01' 
# today = datetime.strptime(specified_month, '%Y-%m-%d')

today=datetime.today()
start_date = (today + relativedelta(months=-25)).strftime('%Y-%m-01')
end_date = (today + relativedelta(months=5)).strftime('%Y-%m-01')
full_date_range = pd.date_range(start=start_date, end=end_date, freq='MS').normalize()

In [12]:
# 創建 ForecastValidator 的實例

fcst_month = 2

forecast_pipeline =  ForecastPIPE(
    preprocessor=preprocessor,
    start_date=start_date,
    end_date=end_date,
    fcst_month=fcst_month,
    product_info=product_info,
    ZSTRATEGY_data=ZSTRATEGY_data
)

##### comparision data preparation

In [ ]:
# data_extractor = DataExtractor()
# benchmark_data= data_extractor.get_prediction_data()
# data_extractor.save_to_csv(benchmark_data, 'benchmark_data')

d:\SCM_indicator\utils\fetch_data.py:138: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  fcst_ori = pd.read_sql(sql_schema_fcst, self.extract_connection)


Data saved to ./Dataset/Fcst(proposed)/benchmark_data_2025-02-24.csv


In [13]:
gloab_demand=create_full_data(actual_data, full_date_range, 'ORDER_QTY')
gloab_demand_pivot=process_data(gloab_demand, 'ORDER_QTY')

benchmark_processor = BenchmarkProcessor()
benchmark_processor.load_data('./Dataset/Fcst(proposed)/benchmark_data_2025-02-24.csv')

d:\SCM_indicator\benchmark_data\benchmark_process.py:13: DtypeWarning: Columns (2,12) have mixed types. Specify dtype option on import or set low_memory=False.
  self.aifcst_postprocess= pd.read_csv(file_path)


##### Run Validation

In [ ]:
final_result=[]
for fcst_month in range(0,6):
    print(f"fcst_month: {fcst_month}")
    forecast_pipeline.fcst_month = fcst_month
    commit_data, eval_processor = forecast_pipeline.run_validation(used_data, open_data_list, benchmark_processor, gloab_demand_pivot)
    final_result.append(commit_data)

fcst_month: 0
ABC類: A


d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100


use random forest model
Training MSE: 0.02
Testing MSE: 0.13
ABC類: B


d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input

use random forest model
Training MSE: 0.07
Testing MSE: 2.83
ABC類: C


...

use random forest model
Training MSE: 0.10
Testing MSE: 0.39
fcst_month: 1
ABC類: A


d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100


use random forest model
Training MSE: 0.02
Testing MSE: 0.85
ABC類: B


d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input

use random forest model
Training MSE: 0.09
Testing MSE: 1.14


##### Evaluation performance 

In [19]:
eval_data=pd.concat(final_result, ignore_index=True)
eval_processor.evaluate_performance(eval_data)

type  number    ACC   WACC
0  所有預測(Model)   15138  99.04   0.00
0    所有預測(MSU)   15138  99.04   0.00
0     所有預測(DS)   15138  99.04   0.00
0    所有預測(AWS)   15138  99.04   0.00
0         所有預測   15138  93.30  16.17
0  所有指標(Model)       0    NaN   0.00
0    所有指標(MSU)       0    NaN   0.00
0     所有指標(DS)       0    NaN   0.00
0    所有指標(AWS)       0    NaN   0.00
0         所有指標       0    NaN   0.00
0  上升指標(Model)       0    NaN   0.00
0    上升指標(MSU)       0    NaN   0.00
0     上升指標(DS)       0    NaN   0.00
0    上升指標(AWS)       0    NaN   0.00
0         上升指標       0    NaN   0.00
0  下降指標(Model)       0    NaN   0.00
0    下降指標(MSU)       0    NaN   0.00
0     下降指標(DS)       0    NaN   0.00
0    下降指標(AWS)       0    NaN   0.00
0         下降指標       0    NaN   0.00

In [15]:
for pd in list(eval_data.query('AIFLAG=="Y"').PD.unique()):
    print(pd)
    print(eval_processor.evaluate_performance(eval_data.query(f'PD=="{pd}" and (ABC_INDICATOR.str.startswith("A") or ABC_INDICATOR.str.startswith("B"))')))
# eval_processor.evaluate_performance(eval_data.query('AIFLAG=="Y"'))

IPC
          type  number    ACC   WACC
0  所有預測(Model)      81   0.00   0.00
0    所有預測(MSU)      81  58.68  73.39
0     所有預測(DS)      81  58.68  73.39
0    所有預測(AWS)      81  60.42  72.46
0         所有預測      81  59.75  73.55
0  所有指標(Model)      18   0.00   0.00
0    所有指標(MSU)      18  73.03  77.08
0     所有指標(DS)      18  73.03  77.08
0    所有指標(AWS)      18  73.27  75.11
0         所有指標      18  72.78  75.17
0  上升指標(Model)       9   0.00   0.00
0    上升指標(MSU)       9  76.14  75.50
0     上升指標(DS)       9  76.14  75.50
0    上升指標(AWS)       9  75.07  75.07
0         上升指標       9  75.47  71.11
0  下降指標(Model)       9   0.00   0.00
0    下降指標(MSU)       9  69.92  77.49
0     下降指標(DS)       9  69.92  77.49
0    下降指標(AWS)       9  71.48  75.13
0         下降指標       9  70.08  76.24
Smart I/O & Communication
          type  number    ACC   WACC
0  所有預測(Model)      51   0.00   0.00
0    所有預測(MSU)      51  50.19  62.55
0     所有預測(DS)      51  51.04  64.71
0    所有預測(AWS)      51  53.67  67.74
0       

In [51]:
eval_processor.evaluate_performance(eval_data.query(f'PD=="{pd}" and AIFLAG=="Y"'))

type  number  ACC  WACC
0  所有預測(Model)       0  NaN   0.0
0    所有預測(MSU)       0  NaN   0.0
0     所有預測(DS)       0  NaN   0.0
0    所有預測(AWS)       0  NaN   0.0
0         所有預測       0  NaN   0.0
0  所有指標(Model)       0  NaN   0.0
0    所有指標(MSU)       0  NaN   0.0
0     所有指標(DS)       0  NaN   0.0
0    所有指標(AWS)       0  NaN   0.0
0         所有指標       0  NaN   0.0
0  上升指標(Model)       0  NaN   0.0
0    上升指標(MSU)       0  NaN   0.0
0     上升指標(DS)       0  NaN   0.0
0    上升指標(AWS)       0  NaN   0.0
0         上升指標       0  NaN   0.0
0  下降指標(Model)       0  NaN   0.0
0    下降指標(MSU)       0  NaN   0.0
0     下降指標(DS)       0  NaN   0.0
0    下降指標(AWS)       0  NaN   0.0
0         下降指標       0  NaN   0.0

##### Run Inference 

In [13]:
final_result=[]
for fcst_month in range(0,6):
    print(f"fcst_month: {fcst_month}")
    forecast_pipeline.fcst_month = fcst_month
    commit_data = forecast_pipeline.run_inference(used_data, open_data_list)
    final_result.append(commit_data)

fcst_month: 0
ABC類: A


d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input

use random forest model
Training MSE: 0.02
Testing MSE: 0.16
ABC類: B


d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input

use random forest model
Training MSE: 0.08
Testing MSE: 0.83
ABC類: C


...

use random forest model
Training MSE: 0.03
Testing MSE: 1.16
ABC類: B


d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input

use random forest model
Training MSE: 0.14
Testing MSE: 2.45
ABC類: C


d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:60: RuntimeWarning: invalid value encountered in scalar divide
  tp_rate = (tp_num / pos_indicator) * 100
d:\SCM_indicator\input_preprocess\indicator_processor.py:63: RuntimeWarning: invalid value encountered in scalar divide
  tn_rate = (tn_num / neg_indicator) * 100
d:\SCM_indicator\input

use random forest model
Training MSE: 0.14
Testing MSE: 0.77


##### 調整pred小於backlog 

In [32]:
final_commit_data = pd.concat(final_result, ignore_index=True)
sorted_df = final_commit_data.sort_values(by=['MATNR', 'FCST_DATE']).reset_index(drop=True)
sorted_df

KeyError: 'MATNR'

In [15]:
import math
from upload_pipeline.opendata_process import get_realtime_opendata

def merge_data(data, data_2):
    merged_data = data.merge(data_2, on='MATNR', how='left')
    return merged_data

def update_fcst_qty( today, merged_data):
    # 更新近期三個月
    
    this_month= today.strftime('%Y%m')
    next_month=(today+relativedelta(months=1)).strftime('%Y%m')
    the_next_month=(today+relativedelta(months=2)).strftime('%Y%m')
    the_3_month=(today+relativedelta(months=3)).strftime('%Y%m')
    the_4_month=(today+relativedelta(months=4)).strftime('%Y%m')
    # 更新 FCST_DATE 為 202501 的資料
    condition_1 = (merged_data['FCST_DATE'] == this_month) & (merged_data['FCST_QTY'] < merged_data['OPEN_QTY'])
    merged_data.loc[condition_1, 'FCST_QTY'] = merged_data.loc[condition_1, 'OPEN_QTY']
    
    # 更新 FCST_DATE 為 202502 的資料
    condition_2= (merged_data['FCST_DATE'] == next_month) & (merged_data['FCST_QTY'] < merged_data['OPEN_QTY_1'])
    merged_data.loc[condition_2, 'FCST_QTY'] = merged_data.loc[condition_2, 'OPEN_QTY_1']
    
    condition_3= (merged_data['FCST_DATE'] == the_next_month) & (merged_data['FCST_QTY'] < merged_data['OPEN_QTY_2'])
    merged_data.loc[condition_3, 'FCST_QTY'] = merged_data.loc[condition_3, 'OPEN_QTY_2']

    condition_4= (merged_data['FCST_DATE'] == the_3_month) & (merged_data['FCST_QTY'] < merged_data['OPEN_QTY_3'])
    merged_data.loc[condition_4, 'FCST_QTY'] = merged_data.loc[condition_4, 'OPEN_QTY_3']

    condition_5= (merged_data['FCST_DATE'] == the_4_month) & (merged_data['FCST_QTY'] < merged_data['OPEN_QTY_4'])
    merged_data.loc[condition_5, 'FCST_QTY'] = merged_data.loc[condition_5, 'OPEN_QTY_4']
    return merged_data

def adjust_fcst_qty(x):
    if x < 8:
        return int(x)
    else:
        return math.ceil(x / 5) * 5

In [16]:

# 計算排除月份
exclude_month = (datetime.today() - relativedelta(months=1)).strftime('%Y/%m/01')

# 獲取即時開放數據
data_extractor = DataExtractor()
product_info = data_extractor.get_product_info()


open_so_curr_20 = data_extractor.get_openso_current()
open_wo_curr_20 = data_extractor.get_openwo_current()
# open_so_curr_20=pd.read_csv('Dataset\Fcst(proposed)\.csv')
# open_wo_curr_20=pd.read_csv('Dataset\Fcst(proposed)\open_wo_curr_2025-01-19.csv')
open_so_final_20, open_wo_final_20 = get_realtime_opendata(open_so_histo, open_so_curr_20, open_wo_histo, open_wo_curr_20, exclude_month)

# 初始化數據預處理器
preprocessor_now = DataPreprocessor(
    product_data=product_info,
    so_data=so_data,
    wo_data=wo_data,
    open_wo_data=open_wo_final_20,
    open_so_data=open_so_final_20
)

# 預處理 SO 數據
so_data_processed = preprocessor_now.so_data_preprocess()

# 合併開放數據
open_data_list = [preprocessor_now.merge_open_so_wo(gap_year=i) for i in range(1, 7)]

# 創建完整數據
open_data_backlog_list = [create_full_data(open_data, full_date_range, 'OPEN_QTY') for open_data in open_data_list]

# 處理數據
open_data_backlog_pivot_list = [process_data(open_data_backlog, 'OPEN_QTY') for open_data_backlog in open_data_backlog_list]

# 初始化合併數據
merged_data = sorted_df

# 合併每個年度的數據
for i in range(5):
    # 取得需要的資料
    data_to_merge = open_data_backlog_pivot_list[i].iloc[:, [0, 26 + i]]
    
    # 將 part_no 欄位重新命名為 MATNR
    data_to_merge.rename(columns={'PART_NO': 'MATNR'}, inplace=True)
    
    # 進行 merge
    merged_data = merge_data(merged_data, data_to_merge)

# 填充缺失值
merged_data = merged_data.fillna(0)

renamed_data = merged_data.rename(columns={
    merged_data.columns[-5]: 'OPEN_QTY',
    merged_data.columns[-4]: 'OPEN_QTY_1',
    merged_data.columns[-3]: 'OPEN_QTY_2',
    merged_data.columns[-2]: 'OPEN_QTY_3',
    merged_data.columns[-1]: 'OPEN_QTY_4'

})

# 確認是否比backlog資料大 
merged_data_update= update_fcst_qty(today, renamed_data)
# 調整為五的倍數 
merged_data_update.loc[:, 'FCST_QTY'] = merged_data_update['FCST_QTY'].apply(adjust_fcst_qty)
upload_data=merged_data_update[['MANDT', 'MATNR', 'WERKS', 'FCST_TYPE', 'FCST_DATE', 'CREATE_DATE',
       'FCST_QTY', 'AIFCST_RATE', 'MOVING_AVG_QTY', 'MOVING_AVG_RATE',
       'EVALUTE_FLAG', 'ALERT_FLAG', 'ZSTRATEGY', 'AI_TREND']]

upload_data

d:\SCM_indicator\utils\fetch_data.py:36: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  product_ori = pd.read_sql(sql_schema_product, self.extract_connection)
d:\SCM_indicator\utils\fetch_data.py:74: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  open_so_c_ori = pd.read_sql(sql_schema_open_so_c, self.extract_connection)
d:\SCM_indicator\utils\fetch_data.py:111: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  open_wo_c_ori = pd.read_sql(sql_schema_open_wo_c, self.extract_connection)


exclude_version: 2025/02/01
exclude_version: 2025/02/01


C:\Users\mt.yang\AppData\Local\Temp\ipykernel_3364\1077072678.py:45: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_to_merge.rename(columns={'PART_NO': 'MATNR'}, inplace=True)
C:\Users\mt.yang\AppData\Local\Temp\ipykernel_3364\1077072678.py:45: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_to_merge.rename(columns={'PART_NO': 'MATNR'}, inplace=True)
C:\Users\mt.yang\AppData\Local\Temp\ipykernel_3364\1077072678.py:45: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.ht

MANDT               MATNR WERKS FCST_TYPE FCST_DATE CREATE_DATE  \
0       168         9792S030000               D    202503    20250305   
1       168         9792S030000               D    202504    20250305   
2       168         9792S030000               D    202505    20250305   
3       168         9792S030000               D    202506    20250305   
4       168         9792S030000               D    202507    20250305   
...     ...                 ...   ...       ...       ...         ...   
15721   168  WOP211K51S42401E-C               D    202504    20250305   
15722   168  WOP211K51S42401E-C               D    202505    20250305   
15723   168  WOP211K51S42401E-C               D    202506    20250305   
15724   168  WOP211K51S42401E-C               D    202507    20250305   
15725   168  WOP211K51S42401E-C               D    202508    20250305   

       FCST_QTY AIFCST_RATE MOVING_AVG_QTY MOVING_AVG_RATE EVALUTE_FLAG  \
0             0           0              0               0            0   
1             0           0              0               0            0   
2             0           0              0               0            0   
3             0           0              0               0            0   
4             0           0              0               0            0   
...         ...         ...            ...             ...          ...   
15721        30           0              0               0            0   
15722        40           0              0               0            0   
15723        35           0              0               0            0   
15724        35           0              0               0            0   
15725        25           0              0               0            0   

      ALERT_FLAG ZSTRATEGY  AI_TREND  
0              0                 0.0  
1              0                 0.0  
2              0                 0.0  
3              0                 0.0  
4              0                 0.0  
...          ...       ...       ...  
15721          0                 0.0  
15722          0                 0.0  
15723          0                 0.0  
15724          0                 0.0  
15725          0                 0.0  

[15726 rows x 14 columns]

##### 上傳資料

In [ ]:
from utils.hana_connection import Upload_Test_Environment,Upload_Deployment_Environment
upload_data.to_csv("Dataset/upload_data_20250305.csv", index=False)

In [22]:
from datetime import datetime, timedelta
upload_data.loc[:, 'FCST_TYPE'] = 'M'
upload_data.loc[:, 'CREATE_DATE'] =  (datetime.now() - timedelta(days=1)).strftime('%Y%m%d')
upload_data

MANDT               MATNR WERKS FCST_TYPE FCST_DATE CREATE_DATE  \
0       168         9792S030000               M    202503    20250304   
1       168         9792S030000               M    202504    20250304   
2       168         9792S030000               M    202505    20250304   
3       168         9792S030000               M    202506    20250304   
4       168         9792S030000               M    202507    20250304   
...     ...                 ...   ...       ...       ...         ...   
15721   168  WOP211K51S42401E-C               M    202504    20250304   
15722   168  WOP211K51S42401E-C               M    202505    20250304   
15723   168  WOP211K51S42401E-C               M    202506    20250304   
15724   168  WOP211K51S42401E-C               M    202507    20250304   
15725   168  WOP211K51S42401E-C               M    202508    20250304   

       FCST_QTY AIFCST_RATE MOVING_AVG_QTY MOVING_AVG_RATE EVALUTE_FLAG  \
0             0           0              0               0            0   
1             0           0              0               0            0   
2             0           0              0               0            0   
3             0           0              0               0            0   
4             0           0              0               0            0   
...         ...         ...            ...             ...          ...   
15721        30           0              0               0            0   
15722        40           0              0               0            0   
15723        35           0              0               0            0   
15724        35           0              0               0            0   
15725        25           0              0               0            0   

      ALERT_FLAG ZSTRATEGY  AI_TREND  
0              0                 0.0  
1              0                 0.0  
2              0                 0.0  
3              0                 0.0  
4              0                 0.0  
...          ...       ...       ...  
15721          0                 0.0  
15722          0                 0.0  
15723          0                 0.0  
15724          0                 0.0  
15725          0                 0.0  

[15726 rows x 14 columns]

In [ ]:
#確認M 和D版本都要上傳到
Upload_Test_Environment(upload_data)

Finish 測試資料100筆上傳測試機


In [30]:
Upload_Deployment_Environment(upload_data)

Finish 上傳正式機


##### 資料檢視

In [24]:
pivot_df =upload_data[['MATNR','FCST_DATE','FCST_QTY']].pivot(index='MATNR',columns="FCST_DATE", values='FCST_QTY')
pivot_df.columns.name = None
pivot_df = pivot_df.reset_index()

ai_trend_df=sorted_df[['MATNR','AI_TREND']].drop_duplicates()
merged_df = pivot_df.merge(ai_trend_df, on='MATNR', how='left')
merged_df

MATNR  202503  202504  202505  202506  202507  202508  \
0            9792S030000       0       0       0       0       0       0   
1         ABDNA-ER-DP551       0      15      15       5       0       0   
2        ABDNA-ER-DP551U      10       6       0      15      10      15   
3         ABDNA-ER-DP553       0       0       7      45      35       7   
4        ABDNA-ER-IN5010      55      45      60      75     120     105   
...                  ...     ...     ...     ...     ...     ...     ...   
2616   WOP210K30S12401-C      30      20      20      20      10      25   
2617   WOP210K31S12401-C      30      15      40      25      30      25   
2618   WOP210K31S12402-C      20      25      25      20      20      30   
2619  WOP210K51S42401E-C      45      55      50      45      45      45   
2620  WOP211K51S42401E-C      40      30      40      35      35      25   

      AI_TREND  
0          0.0  
1          0.0  
2          0.0  
3          0.0  
4          0.0  
...        ...  
2616       0.0  
2617       0.0  
2618      -1.0  
2619       0.0  
2620       0.0  

[2621 rows x 8 columns]

In [26]:
data_to_merge = gloab_demand_pivot.iloc[:, [0, 20, 21, 22, 23, 24, 25]]
data_to_merge.rename(columns={'PART_NO': 'MATNR'}, inplace=True)
past_demand= merge_data(merged_df,data_to_merge)
past_demand['6M Avg.']=past_demand.iloc[:, -6:].mean(axis=1)
past_demand['6M Avg.']=past_demand['6M Avg.'].fillna(0)
past_demand['6M Avg.']=past_demand['6M Avg.'].astype(int)

merged_data = past_demand
for i in range(5):
    data_to_merge = open_data_backlog_pivot_list[i].iloc[:, [0, 26 + i]]
    
    # 將 part_no 欄位重新命名為 MATNR
    data_to_merge.rename(columns={'PART_NO': 'MATNR'}, inplace=True)
    
    # 進行 merge
    merged_data = merge_data(merged_data, data_to_merge)
    
backlog_info=merged_data.fillna(0)


# 確認要重命名的列標籤範圍
fcst_columns = backlog_info.columns[1:7]
histo_columns = backlog_info.columns[8:14]
backlog_columns = backlog_info.columns[15:]

# 重命名列標籤
new_columns = backlog_info.columns.tolist()

# 重命名 FCST(N) 至 FCST(N+5)
for i, col in enumerate(fcst_columns):
    new_columns[backlog_info.columns.get_loc(col)] = f'AIFCST (N+{i})'

# 重命名 Histo(N-6) 至 Histo(N-1)
for i, col in enumerate(histo_columns):
    new_columns[backlog_info.columns.get_loc(col)] = f'Histo (N-{6-i})'

# 重命名 Backlog(N) 至 Backlog(N+3)
for i, col in enumerate(backlog_columns):
    new_columns[backlog_info.columns.get_loc(col)] = f'Backlog (N+{i})'

# 更新 DataFrame 的列標籤
backlog_info.columns = new_columns

product_info_renamed = product_info.rename(columns={'PART_NO': 'MATNR'})
check_df=backlog_info.merge(product_info_renamed [['MATNR', 'PG', 'PD', 'ABC_INDICATOR','AIFLAG']], on='MATNR', how='left')
check_df=check_df.merge(ZSTRATEGY_data, on='MATNR', how='left')
check_df=check_df[['PG', 'PD', 'ABC_INDICATOR','AIFLAG', 'AI_TREND','ZSTRATEGY', 'MATNR', 'AIFCST (N+0)', 'AIFCST (N+1)', 'AIFCST (N+2)', 'AIFCST (N+3)',
       'AIFCST (N+4)', 'AIFCST (N+5)', 'Histo (N-6)',
       'Histo (N-5)', 'Histo (N-4)', 'Histo (N-3)', 'Histo (N-2)',
       'Histo (N-1)', '6M Avg.', 'Backlog (N+0)', 'Backlog (N+1)',
       'Backlog (N+2)','Backlog (N+3)','Backlog (N+4)']]

check_df


C:\Users\mt.yang\AppData\Local\Temp\ipykernel_3364\2974568656.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_to_merge.rename(columns={'PART_NO': 'MATNR'}, inplace=True)
C:\Users\mt.yang\AppData\Local\Temp\ipykernel_3364\2974568656.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_to_merge.rename(columns={'PART_NO': 'MATNR'}, inplace=True)
C:\Users\mt.yang\AppData\Local\Temp\ipykernel_3364\2974568656.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.htm

PG                             PD ABC_INDICATOR AIFLAG  AI_TREND  \
0      ESG      Network Security Platform            C2              0.0   
1     ICWG  Industrial Wireless & Sensing            C2              0.0   
2     ICWG  Industrial Wireless & Sensing            C2              0.0   
3     ICWG  Industrial Wireless & Sensing            C2              0.0   
4     ICWG  Industrial Wireless & Sensing            C2              0.0   
...    ...                            ...           ...    ...       ...   
2616   IAG                        IoT HMI            C3              0.0   
2617   IAG                        IoT HMI            C3              0.0   
2618   IAG                        IoT HMI            C3             -1.0   
2619   IAG                        IoT HMI            C3              0.0   
2620   IAG                        IoT HMI            C3              0.0   

     ZSTRATEGY               MATNR  AIFCST (N+0)  AIFCST (N+1)  AIFCST (N+2)  \
0          NaN         9792S030000             0             0             0   
1          NaN      ABDNA-ER-DP551             0            15            15   
2          NaN     ABDNA-ER-DP551U            10             6             0   
3          NaN      ABDNA-ER-DP553             0             0             7   
4          NaN     ABDNA-ER-IN5010            55            45            60   
...        ...                 ...           ...           ...           ...   
2616       NaN   WOP210K30S12401-C            30            20            20   
2617       NaN   WOP210K31S12401-C            30            15            40   
2618       NaN   WOP210K31S12402-C            20            25            25   
2619       NaN  WOP210K51S42401E-C            45            55            50   
2620       NaN  WOP211K51S42401E-C            40            30            40   

      ...  Histo (N-4)  Histo (N-3)  Histo (N-2)  Histo (N-1)  6M Avg.  \
0     ...          0.0         30.0          0.0          0.0        5   
1     ...         13.0          0.0         10.0          0.0        3   
2     ...          6.0          4.0          1.0          2.0        3   
3     ...        175.0          0.0          0.0          0.0       30   
4     ...         43.0        111.0        117.0        150.0       71   
...   ...          ...          ...          ...          ...      ...   
2616  ...          0.0          0.0         10.0         10.0        3   
2617  ...          0.0          0.0         41.0         19.0       10   
2618  ...          0.0          0.0          4.0         31.0        5   
2619  ...          0.0         20.0         10.0         20.0        8   
2620  ...          0.0          0.0         10.0         10.0        3   

      Backlog (N+0)  Backlog (N+1)  Backlog (N+2)  Backlog (N+3)  \
0               0.0            0.0            0.0            0.0   
1               0.0            0.0            0.0            0.0   
2               3.0            0.0            0.0            2.0   
3               0.0            0.0            0.0            0.0   
4              20.0            0.0            0.0            0.0   
...             ...            ...            ...            ...   
2616           25.0           20.0           20.0           20.0   
2617           15.0            0.0           20.0           20.0   
2618           15.0           11.0            0.0            0.0   
2619           41.0           55.0           20.0           20.0   
2620           40.0            0.0           20.0           20.0   

      Backlog (N+4)  
0               0.0  
1               0.0  
2               0.0  
3               0.0  
4              20.0  
...             ...  
2616            0.0  
2617            0.0  
2618           15.0  
2619           20.0  
2620            0.0  

[2621 rows x 25 columns]

In [27]:
import numpy as np 
eol_part_no_set = set(eol_handler.eol_map_data.PART_NO_NEW.unique())
check_df['EOL_CHECK'] = np.where(check_df['MATNR'].isin(eol_part_no_set), 'Y', 'N')
check_df=check_df[['PG', 'PD', 'ABC_INDICATOR', 'AIFLAG', 'AI_TREND', 'ZSTRATEGY','EOL_CHECK','MATNR',
       'AIFCST (N+0)', 'AIFCST (N+1)', 'AIFCST (N+2)', 'AIFCST (N+3)',
       'AIFCST (N+4)', 'AIFCST (N+5)', 'Histo (N-6)', 'Histo (N-5)',
       'Histo (N-4)', 'Histo (N-3)', 'Histo (N-2)', 'Histo (N-1)', '6M Avg.',
       'Backlog (N+0)', 'Backlog (N+1)', 'Backlog (N+2)', 'Backlog (N+3)',
       'Backlog (N+4)']]

check_df

PG                             PD ABC_INDICATOR AIFLAG  AI_TREND  \
0      ESG      Network Security Platform            C2              0.0   
1     ICWG  Industrial Wireless & Sensing            C2              0.0   
2     ICWG  Industrial Wireless & Sensing            C2              0.0   
3     ICWG  Industrial Wireless & Sensing            C2              0.0   
4     ICWG  Industrial Wireless & Sensing            C2              0.0   
...    ...                            ...           ...    ...       ...   
2616   IAG                        IoT HMI            C3              0.0   
2617   IAG                        IoT HMI            C3              0.0   
2618   IAG                        IoT HMI            C3             -1.0   
2619   IAG                        IoT HMI            C3              0.0   
2620   IAG                        IoT HMI            C3              0.0   

     ZSTRATEGY EOL_CHECK               MATNR  AIFCST (N+0)  AIFCST (N+1)  ...  \
0          NaN         N         9792S030000             0             0  ...   
1          NaN         N      ABDNA-ER-DP551             0            15  ...   
2          NaN         N     ABDNA-ER-DP551U            10             6  ...   
3          NaN         N      ABDNA-ER-DP553             0             0  ...   
4          NaN         N     ABDNA-ER-IN5010            55            45  ...   
...        ...       ...                 ...           ...           ...  ...   
2616       NaN         N   WOP210K30S12401-C            30            20  ...   
2617       NaN         N   WOP210K31S12401-C            30            15  ...   
2618       NaN         N   WOP210K31S12402-C            20            25  ...   
2619       NaN         N  WOP210K51S42401E-C            45            55  ...   
2620       NaN         N  WOP211K51S42401E-C            40            30  ...   

      Histo (N-4)  Histo (N-3)  Histo (N-2)  Histo (N-1)  6M Avg.  \
0             0.0         30.0          0.0          0.0        5   
1            13.0          0.0         10.0          0.0        3   
2             6.0          4.0          1.0          2.0        3   
3           175.0          0.0          0.0          0.0       30   
4            43.0        111.0        117.0        150.0       71   
...           ...          ...          ...          ...      ...   
2616          0.0          0.0         10.0         10.0        3   
2617          0.0          0.0         41.0         19.0       10   
2618          0.0          0.0          4.0         31.0        5   
2619          0.0         20.0         10.0         20.0        8   
2620          0.0          0.0         10.0         10.0        3   

      Backlog (N+0)  Backlog (N+1)  Backlog (N+2)  Backlog (N+3)  \
0               0.0            0.0            0.0            0.0   
1               0.0            0.0            0.0            0.0   
2               3.0            0.0            0.0            2.0   
3               0.0            0.0            0.0            0.0   
4              20.0            0.0            0.0            0.0   
...             ...            ...            ...            ...   
2616           25.0           20.0           20.0           20.0   
2617           15.0            0.0           20.0           20.0   
2618           15.0           11.0            0.0            0.0   
2619           41.0           55.0           20.0           20.0   
2620           40.0            0.0           20.0           20.0   

      Backlog (N+4)  
0               0.0  
1               0.0  
2               0.0  
3               0.0  
4              20.0  
...             ...  
2616            0.0  
2617            0.0  
2618           15.0  
2619           20.0  
2620            0.0  

[2621 rows x 26 columns]

In [ ]:
flag_data=check_df.query('AIFLAG=="Y"').reset_index(drop=True)
flag_data.to_csv('Dataset/check_df-0304_V2.csv', index=False)

##### [ Optional ]刪除backlog(test backlog with eol) 

In [ ]:
eol_old_backlog_wo=eol_open_wo_histo.query('PART_NO in @eol_part_no_set and VERSION=="2025/02/01"')[['PART_NO','VERSION','YM','OPEN_QTY']]
eol_old_backlog_so=eol_open_so_histo.query('PART_NO in @eol_part_no_set and VERSION=="2025/02/01"')[['PART_NO','VERSION','YM','OPEN_QTY']]
eol_old_backlog_total =pd.concat([eol_old_backlog_wo,eol_old_backlog_so])
eol_old_backlog_total['year_month'] =pd.to_datetime(eol_old_backlog_total["YM"], format="%Y/%m/%d")
EOL_full=create_full_data(eol_old_backlog_total, full_date_range, 'OPEN_QTY')
EOL_full_pivot=process_data(EOL_full,'OPEN_QTY')
# EOL_full_pivot
EOL_full_pivot_select= EOL_full_pivot.iloc[:, [0, -6, -5, -4, -3, -2, -1]].copy()
EOL_full_pivot_select.rename(columns={'PART_NO': 'MATNR'}, inplace=True)
EOL_full_pivot_select

check_df_new = check_df.merge(EOL_full_pivot_select, on='MATNR', how='left').fillna(0)
check_df_new

# 取得 'AIFCST (N+0)' 的起始索引
aifcst_start_idx = check_df_new.columns.get_loc('AIFCST (N+0)')

# 取得對應的 EOL_full_pivot_select 開始索引
eol_start_idx = check_df_new.columns.get_loc(EOL_full_pivot_select.columns[1])  # 第一個日期欄位

# 迴圈處理對應欄位
for i in range(6):  # 連續處理 'AIFCST (N+0)' 到 'AIFCST (N+5)' 和 'Histo (N-6)'
    check_col_idx = aifcst_start_idx + i
    eol_col_idx = eol_start_idx + i
    check_df.iloc[:, check_col_idx] = check_df.iloc[:, check_col_idx]- check_df_new.iloc[:, eol_col_idx]